In [1]:
from triagerx.model.module_factory import ModelFactory
from loguru import logger
import torch
import pandas as pd
from sklearn.model_selection import train_test_split
from sentence_transformers import SentenceTransformer
from triagerx.dataset.text_processor import TextProcessor
from tqdm import tqdm

tqdm.pandas()

In [2]:
torch.manual_seed(42)

In [3]:
dataset_path = "/home/mdafifal.mamun/notebooks/triagerX/data/openj9_dataset_6_7_24_last_contrib.csv"

In [4]:
df = pd.read_csv(dataset_path)

In [5]:
df.head()

issue_number                                        issue_title  \
0             2  Build instructions link in the README.md point...   
1             3                  FAQ link in the README is broken    
2             5  Link to DockerFile on build instruction page i...   
3            11  HOWTO Request: Managing changes across depende...   
4            13                  Compilation Output is too Verbose   

                                          issue_body  \
0  The `Build instructions` link in the `README.m...   
1  FAQ link in the README leads to: http://www.ec...   
2  Link for DockerFile on [build instruction page...   
3  Like all projects, OpenJ9 builds on the should...   
4  The output when compiling the OpenJ9 source co...   

                                           issue_url issue_state  \
0  https://github.com/eclipse-openj9/openj9/issues/2      closed   
1  https://github.com/eclipse-openj9/openj9/issues/3      closed   
2  https://github.com/eclipse-openj9/openj9/issues/5      closed   
3  https://github.com/eclipse-openj9/openj9/issue...        open   
4  https://github.com/eclipse-openj9/openj9/issue...      closed   

        creator                   labels        assignees   component  
0  aarongraham9                      NaN  gireeshpunathil         NaN  
1        dorrab                      NaN           mpirvu         NaN  
2       r30shah                      NaN          r30shah         NaN  
3       mgaudet                 question         hzongaro         NaN  
4      rservant  enhancement, comp:build         hzongaro  comp:build

In [6]:
df = df.rename(columns={"assignees": "owner", "issue_body": "description"})
df = df.sort_values(by="issue_number")
df = df[df["owner"].notna()]
# df = df[df["component"].notna()]

In [7]:
target_components = ["comp:vm", "comp:jvmti", "comp:jclextensions", "comp:test", "comp:build", "comp:gc"]
target_components = sorted(target_components)

In [8]:
# Define active user map
vm_users = [
    "pshipton",
    "keithc-ca",
    "gacholio",
    "tajila",
    "babsingh",
    "JasonFengJ9",
    "fengxue-IS",
    "hangshao0",
    "theresa.t.mammarella",
    "ChengJin01",
    "singh264",
    "thallium",
    "ThanHenderson",
]
jvmti_users = ["gacholio", "tajila", "babsingh", "fengxue-IS"]
jclextensions_users = ["JasonFengJ9", "pshipton", "keithc-ca"]
test_users = ["LongyuZhang", "annaibm", "sophiaxu0424", "KapilPowar", "llxia"]
build_users = ["adambrousseau", "mahdipub"]
gc_users = ["dmitripivkine", "amicic", "kangyining", "LinHu2016"]

# Putting them in dictionaries
components = {
    "comp:vm": vm_users,
    "comp:jvmti": jvmti_users,
    "comp:jclextensions": jclextensions_users,
    "comp:test": test_users,
    "comp:build": build_users,
    "comp:gc": gc_users,
}

# expected_users = [user for user_list in components.values() for user in user_list]
# df = df[df["owner"].isin(expected_users)]

# df = df[df["component"].isin(target_components)]

In [9]:
df = df.sort_values(by="issue_number")
df["text"] = df.apply(
        lambda x: "Bug Title: " + str(x["issue_title"]) + "\nBug Description: " + str(x["description"]),
        axis=1,
    )

df.head()

issue_number                                        issue_title  \
0             2  Build instructions link in the README.md point...   
1             3                  FAQ link in the README is broken    
2             5  Link to DockerFile on build instruction page i...   
3            11  HOWTO Request: Managing changes across depende...   
4            13                  Compilation Output is too Verbose   

                                         description  \
0  The `Build instructions` link in the `README.m...   
1  FAQ link in the README leads to: http://www.ec...   
2  Link for DockerFile on [build instruction page...   
3  Like all projects, OpenJ9 builds on the should...   
4  The output when compiling the OpenJ9 source co...   

                                           issue_url issue_state  \
0  https://github.com/eclipse-openj9/openj9/issues/2      closed   
1  https://github.com/eclipse-openj9/openj9/issues/3      closed   
2  https://github.com/eclipse-openj9/openj9/issues/5      closed   
3  https://github.com/eclipse-openj9/openj9/issue...        open   
4  https://github.com/eclipse-openj9/openj9/issue...      closed   

        creator                   labels            owner   component  \
0  aarongraham9                      NaN  gireeshpunathil         NaN   
1        dorrab                      NaN           mpirvu         NaN   
2       r30shah                      NaN          r30shah         NaN   
3       mgaudet                 question         hzongaro         NaN   
4      rservant  enhancement, comp:build         hzongaro  comp:build   

                                                text  
0  Bug Title: Build instructions link in the READ...  
1  Bug Title: FAQ link in the README is broken \n...  
2  Bug Title: Link to DockerFile on build instruc...  
3  Bug Title: HOWTO Request: Managing changes acr...  
4  Bug Title: Compilation Output is too Verbose\n...

In [10]:
# df_train, df_test = train_test_split(df, test_size=0.1, shuffle=False)
df_train = pd.read_csv("/home/mdafifal.mamun/notebooks/triagerX/openj9_train.csv")
df_test = pd.read_csv("/home/mdafifal.mamun/notebooks/triagerX/openj9_test.csv")

In [11]:
expected_users = set(df_test.owner.unique())

In [12]:
sample_threshold = 20
developers = df_train["owner"].value_counts()
filtered_developers = developers.index[developers >= sample_threshold]
df_train = df_train[df_train["owner"].isin(filtered_developers)]

train_owners = set(df_train["owner"])
test_owners = set(df_test["owner"])

unwanted = list(test_owners - train_owners)

df_test = df_test[~df_test["owner"].isin(unwanted)]

logger.info(f"Training data: {len(df_train)}, Validation data: {len(df_test)}")
logger.info(f"Number of developers: {len(df_train.owner.unique())}")

logger.info(f"Train dataset size: {len(df_train)}")
logger.info(f"Test dataset size: {len(df_test)}")

2024-06-19 14:04:47.396 | INFO     | __main__:<module>:13 - Training data: 3323, Validation data: 379
2024-06-19 14:04:47.398 | INFO     | __main__:<module>:14 - Number of developers: 50
2024-06-19 14:04:47.400 | INFO     | __main__:<module>:16 - Train dataset size: 3323
2024-06-19 14:04:47.401 | INFO     | __main__:<module>:17 - Test dataset size: 379


In [13]:
# # Generate label ids
lbl2idx = {}
idx2lbl = {}

train_owners = sorted(train_owners)

for idx, dev in enumerate(train_owners):
    lbl2idx[dev] = idx
    idx2lbl[idx] = dev

df_train["owner_id"] = df_train["owner"].apply(lambda owner: lbl2idx[owner])
df_test["owner_id"] = df_test["owner"].apply(lambda owner: lbl2idx[owner])

In [14]:
df_train = df_train[df_train["component"].notna()]
df_test = df_test[df_test["component"].notna()]

In [15]:
comp_id2label = {}
comp_lbl2id = {}

for i, comp in enumerate(target_components):
    comp_id2label[i] = comp
    comp_lbl2id[comp] = i

In [16]:
base_transformer_models = ["microsoft/deberta-base", "roberta-base"]

In [17]:
developer_model_weights = "/work/disa_lab/projects/triagerx/models/openj9/triagerx_ensemble_u3_4_classes_last_dev_seed42.pt"
component_model_weights = "/work/disa_lab/projects/triagerx/models/openj9/component_triagerx_u3_6_classes_seed42.pt"

In [18]:
logger.debug("Modeling network...")
dev_model = ModelFactory.get_model(
    model_key="triagerx",
    output_size=len(df_train.owner_id.unique()),
    unfrozen_layers=3,
    num_classifiers=3,
    base_models=base_transformer_models,
    dropout=0.2,
    max_tokens=256,
    label_map=idx2lbl,
)

2024-06-19 14:04:47.790 | DEBUG    | __main__:<module>:1 - Modeling network...
2024-06-19 14:04:47.792 | DEBUG    | triagerx.model.module_factory:get_model:54 - Instantiating model of class: <class 'triagerx.model.triagerx_dev_model.TriagerxDevModel'>
2024-06-19 14:04:47.793 | DEBUG    | triagerx.model.module_factory:get_model:65 - Including number of filters and classifiers
2024-06-19 14:04:47.795 | DEBUG    | triagerx.model.triagerx_dev_model:__init__:24 - Loading base transformer models: ['microsoft/deberta-base', 'roberta-base']
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [19]:
dev_model.load_state_dict(torch.load(developer_model_weights))

<All keys matched successfully>

In [20]:
comp_model = ModelFactory.get_model(
    model_key="triagerx",
    output_size=6,
    unfrozen_layers=3,
    num_classifiers=3,
    base_models=["microsoft/deberta-base", "roberta-base"],
    dropout=0.2,
    max_tokens=256,
    label_map=comp_id2label,
)

2024-06-19 14:04:52.146 | DEBUG    | triagerx.model.module_factory:get_model:54 - Instantiating model of class: <class 'triagerx.model.triagerx_dev_model.TriagerxDevModel'>
2024-06-19 14:04:52.147 | DEBUG    | triagerx.model.module_factory:get_model:65 - Including number of filters and classifiers
2024-06-19 14:04:52.149 | DEBUG    | triagerx.model.triagerx_dev_model:__init__:24 - Loading base transformer models: ['microsoft/deberta-base', 'roberta-base']
Some weights of RobertaModel were not initialized from the model checkpoint at roberta-base and are newly initialized: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [21]:
comp_model.load_state_dict(torch.load(component_model_weights))

<All keys matched successfully>

In [22]:
similarity_model = SentenceTransformer("all-mpnet-base-v2")

In [23]:
train_embeddings_path = "/home/mdafifal.mamun/notebooks/triagerX/data/openj9_embeddings/embeddings.npy"

In [24]:
encodings = similarity_model.encode(
    df_train.text.tolist(),
    show_progress_bar=True
)

import numpy as np

np.save(train_embeddings_path, encodings)

Batches:   0%|          | 0/83 [00:00<?, ?it/s]

In [25]:
from datetime import datetime
import json
import os
from collections import defaultdict
from typing import Dict, List, Tuple

import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import torch.nn.functional as F
from loguru import logger
from sentence_transformers import util

from triagerx.dataset.text_processor import TextProcessor
from triagerx.model.prediction_model import PredictionModel


class TriagerX:
    """
    A class for recommending developers and components for issues based on prediction models
    and similarity measures.
    """

    def __init__(
        self,
        component_prediction_model: PredictionModel,
        developer_prediction_model: PredictionModel,
        similarity_model: nn.Module,
        train_data: pd.DataFrame,
        train_embeddings: str,
        issues_path: str,
        developer_id_map: Dict[str, int],
        component_id_map: Dict[str, int],
        component_developers_map: Dict[str, List[str]],
        device: str,
    ) -> None:
        """
        Initializes the TriagerX system with models, data, and configurations.

        Args:
            component_prediction_model (PredictionModel): Model to predict components.
            developer_prediction_model (PredictionModel): Model to predict developers.
            similarity_model (nn.Module): Model to compute similarity between issues.
            train_data (pd.DataFrame): Training data containing issue information.
            train_embeddings (str): Path to precomputed embeddings of training issues.
            issues_path (str): Path to the directory containing issue files.
            developer_id_map (Dict[str, int]): Mapping from developer names to IDs.
            component_id_map (Dict[str, int]): Mapping from component names to IDs.
            component_developers_map (Dict[str, List[str]]): Mapping from components to associated developers.
            device (str): Device to run the models on (e.g., 'cpu' or 'cuda').
        """
        self._component_prediction_model = component_prediction_model.to(device)
        self._developer_prediction_model = developer_prediction_model.to(device)
        self._similarity_model = similarity_model
        self._device = device
        self._train_data = train_data
        self._issues_path = issues_path
        self._all_issues = os.listdir(issues_path)
        self._developer2id_map = developer_id_map
        self._component2id_map = component_id_map
        self._id2developer_map = {idx: dev for dev, idx in developer_id_map.items()}
        self._id2component_map = {idx: comp for comp, idx in component_id_map.items()}
        self._component_developers_map = component_developers_map
        self._expected_developers = expected_users
        logger.debug(f"Using device: {device}")
        logger.debug("Loading embeddings for existing issues...")
        self._all_embeddings = np.load(train_embeddings)

    def get_recommendation(
        self, issue: str, k_comp: int, k_dev: int, k_rank: int, similarity_threshold: float
    ) -> Dict[str, List]:
        """
        Generates recommendations for developers and components for a given issue.

        Args:
            issue (str): The issue description.
            k_comp (int): Number of top components to predict.
            k_dev (int): Number of top developers to recommend.
            k_rank (int): Number of developers to rank.
            similarity_threshold (float): Similarity threshold to filter similar issues.

        Returns:
            Dict[str, List]: A dictionary with predicted components, developers, and their scores.
        """
        logger.debug("Predicting components...")
        comp_prediction_score, predicted_components = self._get_predicted_components(issue, k_comp)
        predicted_components_name = [self._id2component_map[idx] for idx in predicted_components]
        logger.info(f"Predicted components: {predicted_components_name}")

        logger.debug("Generating developer recommendations...")
        dev_prediction_score, predicted_devs = self._get_recommendation_from_dev_model(issue, k_rank)
        predicted_developers_name = [self._id2developer_map[idx] for idx in predicted_devs]
        logger.info(f"Recommended developers: {predicted_developers_name}")

        logger.debug("Generating recommendations by similarity...")
        dev_predictions_by_similarity = self._get_recommendation_by_similarity(
            issue, predicted_components, k_dev, k_rank, similarity_threshold
        )
        similar_issue_devs = [dev_sim for dev_sim, _ in dev_predictions_by_similarity]
        logger.info(f"Recommended developers by issue similarity: {similar_issue_devs}")

        logger.debug("Aggregating rankings...")
        rank_lists = [predicted_developers_name, similar_issue_devs]
        aggregated_rank = self._aggregate_rank(rank_lists)[:k_dev]
        logger.info(f"Recommended developers by ranking aggregation: {aggregated_rank}")

        recommendations = {
            "predicted_components": predicted_components_name,
            "comp_prediction_score": comp_prediction_score,
            "predicted_developers": predicted_developers_name[:k_dev],
            "dev_prediction_score": dev_prediction_score,
            "similar_devs": dev_predictions_by_similarity,
            "combined_ranking": aggregated_rank,
        }

        return recommendations

    def _aggregate_rank(self, rank_lists: List[List[str]]) -> List[str]:
        """
        Aggregates rankings from different lists using Borda count.

        Args:
            rank_lists (List[List[str]]): Lists of rankings to aggregate.

        Returns:
            List[str]: Aggregated ranking.
        """
        borda_scores = defaultdict(int)
        for rank_list in rank_lists:
            for i, item in enumerate(rank_list):
                borda_scores[item] += len(rank_list) - i
        sorted_items = sorted(borda_scores.items(), key=lambda x: x[1], reverse=True)
        return [item[0] for item in sorted_items]

    def _get_recommendation_from_dev_model(self, issue: str, k: int) -> Tuple[List[float], List[int]]:
        """
        Generates developer recommendations using the developer prediction model.

        Args:
            issue (str): The issue description.
            k (int): Number of top developers to recommend.

        Returns:
            Tuple[List[float], List[int]]: Scores and indices of the top developers.
        """
        self._developer_prediction_model.eval()
        with torch.no_grad():
            tokenized_issue = self._developer_prediction_model.tokenize_text(issue)
            predictions = self._developer_prediction_model(tokenized_issue)
        output = torch.sum(torch.stack(predictions), 0)
        prediction_score, predicted_devs = output.topk(k, 1, True, True)
        return (
            F.softmax(prediction_score.squeeze(dim=0), dim=0).cpu().numpy().tolist(),
            predicted_devs.squeeze(dim=0).cpu().numpy().tolist()
        )

    def _get_predicted_components(self, issue: str, k: int) -> Tuple[List[float], List[int]]:
        """
        Generates component predictions using the component prediction model.

        Args:
            issue (str): The issue description.
            k (int): Number of top components to predict.

        Returns:
            Tuple[List[float], List[int]]: Scores and indices of the top components.
        """
        self._component_prediction_model.eval()
        with torch.no_grad():
            tokenized_issue = self._component_prediction_model.tokenize_text(issue)
            predictions = self._component_prediction_model(tokenized_issue)
        output = torch.sum(torch.stack(predictions), 0)
        prediction_score, predicted_components = output.topk(k, 1, True, True)
        return (
            F.softmax(prediction_score.squeeze(dim=0), dim=0).cpu().numpy().tolist(),
            predicted_components.squeeze(dim=0).cpu().numpy().tolist()
        )

    def _get_recommendation_by_similarity(
        self, issue: str, predicted_components: List[int], k_dev: int, k_issue: int, similarity_threshold: float
    ) -> List[Tuple[str, float]]:
        """
        Generates developer recommendations based on issue similarity.

        Args:
            issue (str): The issue description.
            predicted_components (List[int]): Predicted component IDs.
            k_dev (int): Number of top developers to recommend.
            k_issue (int): Number of top similar issues to consider.
            similarity_threshold (float): Similarity threshold to filter similar issues.

        Returns:
            List[Tuple[str, float]]: Developers and their similarity scores.
        """
        similar_issues = self._get_top_k_similar_issues(issue, k_issue, similarity_threshold)
        historical_contribution = self._get_historical_contributors(similar_issues, predicted_components)
        logger.debug(historical_contribution)
        return historical_contribution[:k_dev]
    
    def _get_historical_contributors(
        self, similar_issues: List[Tuple[int, float]], predicted_component_ids: List[int]
    ) -> List[Tuple[str, float]]:
        """
        Retrieves historical contributors from similar issues and ranks them.

        Args:
            similar_issues (List[Tuple[int, float]]): List of similar issue indices and similarity scores.
            predicted_component_ids (List[int]): Predicted component IDs.

        Returns:
            List[Tuple[str, float]]: Ranked developers and their contribution scores.
        """
        user_contribution_counts = {}
        skipped_users = set()
        for issue_index, sim_score in similar_issues:
            base_points = 1
            issue = self._train_data.iloc[issue_index]
            # if self._component2id_map.get(issue.component) not in predicted_component_ids:
            #     logger.warning(
            #         f"Skipping issue as label id {self._component2id_map.get(issue.component)} did not match with any of {predicted_component_ids}"
            #     )
            #     continue
            issue_number = issue.issue_number
            contributors = self._get_contribution_data(issue_number)
            for key, users in contributors.items():
                for user_data in users:
                    user = user_data[0]
                    created_at = user_data[1] if len(user_data) > 1 else None
                    
                    if user not in self._expected_developers:
                        skipped_users.add(user)
                        continue

                    contribution_point = 1
                    if key in ["pull_request", "commits"]:
                        contribution_point = 1.5
                    elif key in ["last_assignment", "direct_assignment"]:
                        contribution_point = 2

                    # Calculate time decay only if created_at is available
                    time_decay = 1
                    if created_at:
                        contribution_date = datetime.strptime(created_at, "%Y-%m-%dT%H:%M:%SZ")
                        days_since_contribution = (datetime.now() - contribution_date).days
                        time_decay = 1 / (1 + days_since_contribution / 30)

                        print("Contribution date:", contribution_date)
                        print("Time decay:", time_decay)

                    if user in self._component_developers_map.get(issue.component, []):
                        user_contribution_counts[user] = (
                            user_contribution_counts.get(user, 0) + base_points * contribution_point * time_decay
                        )
                    else:
                        user_contribution_counts[user] = (
                            user_contribution_counts.get(user, 0) + base_points * contribution_point * time_decay
                        )
        if skipped_users:
            logger.warning(
                f"Skipped users: {skipped_users} because they don't exist in the expected developers list"
            )
        return sorted(user_contribution_counts.items(), key=lambda x: x[1], reverse=True)

    def _get_contribution_data(self, issue_number: int) -> Dict[str, List[Tuple[str, str]]]:
        """
        Retrieves contribution data for a given issue.

        Args:
            issue_number (int): Issue number.

        Returns:
            Dict[str, List[Tuple[str, str]]]: Contribution data categorized by type of contribution,
                                            including the contributor and the contribution date.
        """
        contributions = {}
        issue_file = f"{issue_number}.json"
        last_assignment = None
        if issue_file in self._all_issues:
            with open(os.path.join(self._issues_path, issue_file), "r") as file:
                issue = json.load(file)
                assignees = issue.get("assignees", [])
                assignee_logins = [(assignee["login"], None) for assignee in assignees] if assignees else []
                contributions["direct_assignment"] = assignee_logins
                timeline = issue.get("timeline_data", [])
                pull_requests, commits, discussion = [], [], []
                for timeline_event in timeline:
                    event = timeline_event.get("event")
                    created_at = timeline_event.get("created_at")
                    if event == "cross-referenced" and timeline_event["source"].get("issue", {}).get("pull_request"):
                        actor = timeline_event["actor"]["login"]
                        pull_requests.append((actor, created_at))
                        last_assignment = actor
                    elif event == "referenced" and timeline_event.get("commit_url"):
                        actor = timeline_event["actor"]["login"]
                        commits.append((actor, created_at))
                        last_assignment = actor
                    elif event == "commented":
                        actor = timeline_event["actor"]["login"]
                        discussion.append((actor, created_at))
                contributions["pull_request"] = pull_requests
                contributions["commits"] = commits
                contributions["discussion"] = discussion
                contributions["last_assignment"] = [(last_assignment, None)] if last_assignment else []
        return contributions

    def _get_top_k_similar_issues(self, issue: str, k: int, threshold: float) -> List[Tuple[int, float]]:
        """
        Retrieves the top-k similar issues to a given issue based on similarity threshold.

        Args:
            issue (str): The issue description.
            k (int): Number of top similar issues to retrieve.
            threshold (float): Similarity threshold to filter similar issues.

        Returns:
            List[Tuple[int, float]]: Indices and similarity scores of the top similar issues.
        """
        test_embed = self._similarity_model.encode(issue)
        cos_sim = util.cos_sim(test_embed, self._all_embeddings)
        topk_values, topk_indices = torch.topk(cos_sim, k=k)
        topk_values = topk_values.cpu().numpy()[0]
        topk_indices = topk_indices.cpu().numpy()[0]
        return [
            (idx, sim_score) for idx, sim_score in zip(topk_indices, topk_values) if sim_score >= threshold
        ]


In [26]:
trx = TriagerX(
    component_prediction_model=comp_model,
    developer_prediction_model=dev_model,
    similarity_model=similarity_model,
    issues_path="/home/mdafifal.mamun/notebooks/triagerX/data/openj9_issue_data_6_7_24",
    train_embeddings=train_embeddings_path,
    component_developers_map=components,
    developer_id_map=lbl2idx,
    component_id_map=comp_lbl2id,
    train_data=df_train,
    device="cuda"
)

2024-06-19 14:05:13.590 | DEBUG    | __main__:__init__:66 - Using device: cuda
2024-06-19 14:05:13.592 | DEBUG    | __main__:__init__:67 - Loading embeddings for existing issues...


In [27]:
def get_recommendation(test_idx, k_comp, k_dev, k_rank, sim):
    test_data = df_test.iloc[test_idx]

    print("Issue URL: ", test_data["issue_url"])
    print("Actual owner: ", test_data["owner"])
    print("Actual component: ", test_data["component"])

    return trx.get_recommendation(
        test_data.text,
        k_comp=k_comp,
        k_dev=k_dev,
        k_rank=k_rank,
        similarity_threshold=sim
    )

In [28]:
recommendations = []

for i in range(len(df_test)):
    rec = get_recommendation(i, k_comp=3, k_dev=3, k_rank=10, sim=0.6)
    recommendations.append(rec)

2024-06-19 14:05:13.796 | DEBUG    | __main__:get_recommendation:86 - Predicting components...


Issue URL:  https://github.com/eclipse-openj9/openj9/issues/17734
Actual owner:  a7ehuo
Actual component:  comp:jit


2024-06-19 14:05:14.006 | INFO     | __main__:get_recommendation:89 - Predicted components: ['comp:vm', 'comp:gc', 'comp:test']
2024-06-19 14:05:14.008 | DEBUG    | __main__:get_recommendation:91 - Generating developer recommendations...
2024-06-19 14:05:14.060 | INFO     | __main__:get_recommendation:94 - Recommended developers: ['mpirvu', 'a7ehuo', 'hzongaro', 'dsouzai', 'JasonFengJ9', 'r30shah', 'babsingh', 'theresa-m', 'ChengJin01', '0dvictor']
2024-06-19 14:05:14.062 | DEBUG    | __main__:get_recommendation:96 - Generating recommendations by similarity...
2024-06-19 14:05:14.120 | WARNING  | __main__:_get_historical_contributors:260 - Skipped users: {'IBMJimmyk', 'manashaVetrivelu', 'R-Santhir', 'fjeremic', 'DanHeidinga', 'mikezhang1234567890', 'dchopra001', 'liqunl', 'cathyzhyi', 'zl-wang', 'andrewcraik', 'dylanjtuttle'} because they don't exist in the expected developers list
2024-06-19 14:05:14.122 | DEBUG    | __main__:_get_recommendation_by_similarity:198 - [('pshipton', 7.54

Contribution date: 2019-11-15 13:17:00
Time decay: 0.017564402810304452
Contribution date: 2019-11-15 13:15:55
Time decay: 0.017564402810304452
Contribution date: 2019-11-15 13:20:33
Time decay: 0.017564402810304452
Contribution date: 2019-11-15 13:08:40
Time decay: 0.017564402810304452
Contribution date: 2023-04-27 16:54:05
Time decay: 0.06696428571428571
Contribution date: 2023-05-03 20:00:57
Time decay: 0.06787330316742082
Contribution date: 2023-05-26 13:52:21
Time decay: 0.07142857142857142
Contribution date: 2023-06-15 12:15:45
Time decay: 0.075
Contribution date: 2023-06-27 18:13:17
Time decay: 0.07751937984496124
Contribution date: 2023-06-27 18:09:37
Time decay: 0.07751937984496124
Contribution date: 2023-06-27 18:10:24
Time decay: 0.07751937984496124
Contribution date: 2023-06-27 18:13:01
Time decay: 0.07751937984496124
Contribution date: 2023-06-26 23:24:37
Time decay: 0.07731958762886598
Contribution date: 2023-06-26 23:28:24
Time decay: 0.07731958762886598
Contribution dat

2024-06-19 14:05:14.325 | INFO     | __main__:get_recommendation:89 - Predicted components: ['comp:vm', 'comp:gc', 'comp:test']
2024-06-19 14:05:14.327 | DEBUG    | __main__:get_recommendation:91 - Generating developer recommendations...
2024-06-19 14:05:14.365 | INFO     | __main__:get_recommendation:94 - Recommended developers: ['BradleyWood', 'ymanton', 'a7ehuo', 'dsouzai', 'Mesbah-Alam', 'hangshao0', 'hzongaro', 'jdmpapin', 'nbhuiyan', 'knn-k']
2024-06-19 14:05:14.367 | DEBUG    | __main__:get_recommendation:96 - Generating recommendations by similarity...
2024-06-19 14:05:14.411 | WARNING  | __main__:_get_historical_contributors:260 - Skipped users: {'EmanElsaban', 'dchopra001', 'vij-singh', 'dmitry-ten', 'DanHeidinga'} because they don't exist in the expected developers list
2024-06-19 14:05:14.413 | DEBUG    | __main__:_get_recommendation_by_similarity:198 - [('gita-omr', 5.082215510420037), ('nbhuiyan', 4.460734529111788), ('pshipton', 4.058321986448303), ('JasonFengJ9', 2.9877

...

Contribution date: 2019-04-17 12:13:53
Time decay: 0.015625
Contribution date: 2019-02-07 16:10:36
Time decay: 0.015090543259557344
Contribution date: 2019-04-09 01:29:16
Time decay: 0.015560165975103735
Contribution date: 2021-01-08 23:53:50
Time decay: 0.023310023310023312
Contribution date: 2021-01-19 19:45:25
Time decay: 0.023510971786833857
Contribution date: 2021-01-19 19:56:26
Time decay: 0.023510971786833857
Contribution date: 2021-01-20 16:11:57
Time decay: 0.023529411764705882
Contribution date: 2021-01-21 16:31:59
Time decay: 0.02354788069073783
Contribution date: 2021-01-22 16:30:20
Time decay: 0.023566378633150042
Contribution date: 2021-01-29 17:45:41
Time decay: 0.023696682464454975
Contribution date: 2021-01-19 19:44:21
Time decay: 0.023510971786833857
Contribution date: 2021-01-19 19:55:50
Time decay: 0.023510971786833857
Contribution date: 2021-01-20 16:10:53
Time decay: 0.023529411764705882
Contribution date: 2021-01-20 17:13:25
Time decay: 0.023529411764705882
Contr

2024-06-19 14:05:49.541 | DEBUG    | __main__:_get_recommendation_by_similarity:198 - [('JasonFengJ9', 2.049342105263158), ('keithc-ca', 0.03289473684210526)]
2024-06-19 14:05:49.542 | INFO     | __main__:get_recommendation:101 - Recommended developers by issue similarity: ['JasonFengJ9', 'keithc-ca']
2024-06-19 14:05:49.544 | DEBUG    | __main__:get_recommendation:103 - Aggregating rankings...
2024-06-19 14:05:49.545 | INFO     | __main__:get_recommendation:106 - Recommended developers by ranking aggregation: ['gita-omr', 'fengxue-IS', 'keithc-ca']
2024-06-19 14:05:49.546 | DEBUG    | __main__:get_recommendation:86 - Predicting components...
2024-06-19 14:05:49.585 | INFO     | __main__:get_recommendation:89 - Predicted components: ['comp:vm', 'comp:gc', 'comp:build']
2024-06-19 14:05:49.587 | DEBUG    | __main__:get_recommendation:91 - Generating developer recommendations...
2024-06-19 14:05:49.624 | INFO     | __main__:get_recommendation:94 - Recommended developers: ['gacholio', 'Br

Contribution date: 2022-01-18 15:46:29
Time decay: 0.03289473684210526
Contribution date: 2022-01-18 16:21:05
Time decay: 0.03289473684210526
Issue URL:  https://github.com/eclipse-openj9/openj9/issues/19546
Actual owner:  nbhuiyan
Actual component:  comp:jit
Contribution date: 2021-01-22 21:55:52
Time decay: 0.023566378633150042
Contribution date: 2021-02-18 03:53:04
Time decay: 0.024057738572574178
Contribution date: 2021-02-18 03:53:16
Time decay: 0.024057738572574178
Contribution date: 2021-02-18 23:00:06
Time decay: 0.024077046548956663
Contribution date: 2021-02-19 21:13:08
Time decay: 0.024096385542168676
Contribution date: 2021-02-19 21:39:12
Time decay: 0.024096385542168676
Contribution date: 2021-02-22 15:33:13
Time decay: 0.024154589371980676
Contribution date: 2021-02-22 17:12:16
Time decay: 0.024154589371980676
Contribution date: 2021-02-22 17:13:19
Time decay: 0.024154589371980676
Contribution date: 2021-03-07 12:52:07
Time decay: 0.024390243902439025
Contribution date: 2

2024-06-19 14:05:49.768 | WARNING  | __main__:_get_historical_contributors:260 - Skipped users: {'andrew-m-leonard', 'irinarada', 'pdbain-ibm', 'mnalam-p', 'liqunl', 'groeges', 'zl-wang', 'DanHeidinga'} because they don't exist in the expected developers list
2024-06-19 14:05:49.770 | DEBUG    | __main__:_get_recommendation_by_similarity:198 - [('JasonFengJ9', 12.656381950929182), ('babsingh', 9.567490895237489), ('ChengJin01', 5.2315852637342735), ('llxia', 2.134640536128882), ('hzongaro', 2.117583108062168), ('fengxue-IS', 2.0908789073485092), ('mpirvu', 2.0211864406779663), ('pshipton', 0.5396476606249644), ('tajila', 0.20509566496792858), ('theresa-m', 0.20454665146526757), ('0xdaryl', 0.08766954136633001), ('gacholio', 0.035135739361091475), ('r30shah', 0.02284263959390863), ('gita-omr', 0.015197568389057751)]
2024-06-19 14:05:49.771 | INFO     | __main__:get_recommendation:101 - Recommended developers by issue similarity: ['JasonFengJ9', 'babsingh', 'ChengJin01']
2024-06-19 14:05

Contribution date: 2021-12-06 21:24:46
Time decay: 0.031413612565445025
Contribution date: 2022-01-20 16:16:28
Time decay: 0.03296703296703297
Contribution date: 2022-02-04 15:02:53
Time decay: 0.0335195530726257
Contribution date: 2021-12-06 21:23:34
Time decay: 0.031413612565445025
Contribution date: 2021-12-06 21:26:48
Time decay: 0.031413612565445025
Contribution date: 2021-12-07 18:46:29
Time decay: 0.031446540880503145
Contribution date: 2022-01-20 16:14:45
Time decay: 0.03296703296703297
Contribution date: 2022-01-24 23:34:05
Time decay: 0.033112582781456956
Contribution date: 2022-01-24 23:37:07
Time decay: 0.033112582781456956
Contribution date: 2022-01-24 23:56:54
Time decay: 0.033112582781456956
Contribution date: 2022-01-24 23:59:54
Time decay: 0.033112582781456956
Contribution date: 2022-02-01 16:48:28
Time decay: 0.03340757238307349
Contribution date: 2022-02-02 14:39:05
Time decay: 0.033444816053511704
Contribution date: 2022-02-02 21:46:03
Time decay: 0.0334448160535117

In [29]:
combined_total = 0
dl_total = 0
sim_total = 0

for idx in range(len(df_test)):
    actual = df_test.iloc[idx]["owner"]
    combined_recommended = recommendations[idx]["combined_ranking"]
    dl_recommended = recommendations[idx]["predicted_developers"]
    sim_recommended = recommendations[idx]["similar_devs"]

    if sim_recommended:
        sim_recommended = [s[0] for s in sim_recommended]

    print(idx, end=" ")

    if actual in combined_recommended:
        print("Comb,", end="")
        combined_total += 1

    if actual in dl_recommended:
        print("DL,", end="")
        dl_total += 1

    if actual in sim_recommended:
        print("Sim", end="")
        sim_total += 1

    print("===")

0 Comb,DL,Sim===
1 ===
2 ===
3 Comb,DL,Sim===
4 Comb,DL,Sim===
5 Comb,DL,Sim===
6 ===
7 Comb,DL,Sim===
8 Comb,DL,Sim===
9 Comb,DL,Sim===
10 ===
11 ===
12 Comb,DL,Sim===
13 Comb,DL,===
14 Comb,DL,Sim===
15 ===
16 ===
17 ===
18 ===
19 Comb,DL,Sim===
20 ===
21 ===
22 ===
23 Comb,DL,Sim===
24 Comb,DL,Sim===
25 Comb,DL,Sim===
26 Comb,DL,===
27 Comb,DL,Sim===
28 Comb,DL,Sim===
29 Comb,DL,Sim===
30 Comb,DL,===
31 Comb,DL,===
32 Comb,DL,===
33 ===
34 ===
35 Comb,DL,===
36 Comb,DL,Sim===
37 Comb,DL,===
38 ===
39 Comb,DL,Sim===
40 ===
41 ===
42 Comb,DL,===
43 Comb,DL,===
44 Comb,DL,Sim===
45 Comb,DL,===
46 Comb,DL,Sim===
47 Comb,DL,Sim===
48 ===
49 ===
50 Comb,DL,===
51 ===
52 ===
53 ===
54 Comb,DL,Sim===
55 ===
56 ===
57 ===
58 Comb,DL,Sim===
59 Comb,DL,Sim===
60 Comb,DL,Sim===
61 Comb,DL,===
62 Comb,DL,Sim===
63 ===
64 Comb,DL,Sim===
65 Comb,DL,Sim===
66 Comb,DL,Sim===
67 ===
68 Comb,DL,===
69 ===
70 ===
71 Comb,DL,===
72 Comb,DL,Sim===
73 Comb,DL,===
74 ===
75 Comb,DL,Sim===
76 ===
77 Comb,DL

In [30]:
dl_total/len(df_test), sim_total/len(df_test), combined_total/len(df_test)

(0.46075085324232085, 0.4232081911262799, 0.49146757679180886)

In [31]:
get_recommendation(99, k_comp=3, k_dev=3, k_rank=10, sim=0.6)

2024-06-19 14:05:50.689 | DEBUG    | __main__:get_recommendation:86 - Predicting components...
2024-06-19 14:05:50.723 | INFO     | __main__:get_recommendation:89 - Predicted components: ['comp:vm', 'comp:build', 'comp:jclextensions']
2024-06-19 14:05:50.725 | DEBUG    | __main__:get_recommendation:91 - Generating developer recommendations...
2024-06-19 14:05:50.757 | INFO     | __main__:get_recommendation:94 - Recommended developers: ['fengxue-IS', 'gacholio', 'pshipton', 'hangshao0', 'tajila', 'babsingh', 'keithc-ca', 'pdbain-ibm', 'llxia', 'EricYangIBM']
2024-06-19 14:05:50.759 | DEBUG    | __main__:get_recommendation:96 - Generating recommendations by similarity...
2024-06-19 14:05:50.772 | DEBUG    | __main__:_get_recommendation_by_similarity:198 - []
2024-06-19 14:05:50.773 | INFO     | __main__:get_recommendation:101 - Recommended developers by issue similarity: []
2024-06-19 14:05:50.775 | DEBUG    | __main__:get_recommendation:103 - Aggregating rankings...
2024-06-19 14:05:50.

Issue URL:  https://github.com/eclipse-openj9/openj9/issues/18318
Actual owner:  gacholio
Actual component:  comp:vm


{'predicted_components': ['comp:vm', 'comp:build', 'comp:jclextensions'],
 'comp_prediction_score': [0.9999874830245972,
  1.1786803952418268e-05,
  7.318121788557619e-07],
 'predicted_developers': ['fengxue-IS', 'gacholio', 'pshipton'],
 'dev_prediction_score': [0.5909454822540283,
  0.2560594379901886,
  0.09028230607509613,
  0.02303057163953781,
  0.013189655728638172,
  0.009397068060934544,
  0.008694014512002468,
  0.0037875911220908165,
  0.0027411498595029116,
  0.0018727846909314394],
 'similar_devs': [],
 'combined_ranking': ['fengxue-IS', 'gacholio', 'pshipton']}

In [32]:
anal_id = 47

print(df_test.iloc[anal_id]["issue_url"])
df_test.iloc[anal_id], recommendations[anal_id]

https://github.com/eclipse-openj9/openj9/issues/17962


(Unnamed: 0                                                   7258
 issue_number                                                17962
 issue_title     testDDRExtJunit_FindExtThread Failed to constr...
 description     testDDRExtJunit_FindExtThread_0\r\n```\r\n    ...
 issue_url       https://github.com/eclipse-openj9/openj9/issue...
 issue_state                                                  open
 creator                                                  pshipton
 labels                                      comp:vm, test failure
 owner                                                    pshipton
 component                                                 comp:vm
 text            Bug Title: testDDRExtJunit_FindExtThread Faile...
 owner_id                                                       41
 Name: 59, dtype: object,
 {'predicted_components': ['comp:vm', 'comp:test', 'comp:gc'],
  'comp_prediction_score': [0.8749904036521912,
   0.12500955164432526,
   1.1886748296774385e-07],
  'pred